<a href="https://colab.research.google.com/github/JIRUWANG1997/-keras-stacking-keras-with-tf2.0/blob/master/Untitled9.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
pip install patool

In [2]:
# import patoolib
# patoolib.extract_archive("/content/lemm_stop.rar", outdir="/content/sample_data")

In [57]:
import os
import glob
import re
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from tkinter import _flatten
import math
import numpy as np
import random
from sklearn.naive_bayes import MultinomialNB,BernoulliNB
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.svm import SVC

##### **Parameter**:  
dir:  file name for part1~10  
##### **Function**:
For all the .txt files in one part file, split spam and legit files
##### **return**:
spam and legit files in part1 or part2 or...

In [4]:
def get_data(dir):
  content_legit = []
  content_spam = []
  legit_mails = glob.glob("/content/sample_data/lemm_stop/" + dir + "/*msg?.txt")
  spam_mails = glob.glob("/content/sample_data/lemm_stop/" + dir + "/spmsg*.txt")
  for legit_mail in legit_mails:
    f_legit = open(legit_mail, "r")
    each_mail = ""
    for idx,eachLine in enumerate(f_legit):
      if eachLine == "\n":
        continue
      # print(each_mail)
      each_mail+= eachLine.lower() 
    content_legit.append(each_mail)
  for spam_mail in spam_mails:
    f_spam = open(spam_mail, "r")
    each_mail = ""
    for idx,eachLine in enumerate(f_spam):
      if eachLine == "\n":
        continue
      each_mail+= eachLine.lower()
    content_spam.append(each_mail)
  # print(len(content_spam))
  # print(len(content_legit))
  return content_spam,content_legit

In [5]:
''' TEST  '''
# x,y = get_data("part9")
# print(x[10])
# print(len(y))
# # print(y[10])

' TEST  '

##### **Parameter**:  
dataset_dir:  lemm_stop
##### **Function**:
build train and test dataset
##### **return**:
train_x, train_y, test_x, test_y

In [6]:
def split_test_train(dataset_dir):
  print('Loading dataset')
  f = os.listdir(dataset_dir)
  train_data = []
  train_class = []
  test_data = []
  test_class = []
  for file_name in f:
    if file_name != "part10":
      spam_mail, legit_mail = get_data(file_name)
      # print(len(spam_mail),len(legit_mail))
      train_data += spam_mail
      n = [1 for i in range(len(spam_mail))]
      train_class += n
      train_data += legit_mail
      n = [0 for i in range(len(legit_mail))]
      train_class+=n
      # print(len(train_data))
    else:
      spam_mail, legit_mail = get_data(file_name)
      # print(len(spam_mail))
      # print(len(legit_mail))
      test_data+=spam_mail
      n = [1 for i in range(len(spam_mail))]
      test_class+=n
      test_data+=legit_mail
      n = [0 for i in range(len(legit_mail))]
      test_class+=n

  return train_data,train_class,test_data,test_class

In [7]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
# print(len(train_data))
print(len(test_data))

Loading dataset
291


##### **function**:
split word in train/test dataset

In [8]:
def get_word_token(data):
  vectorizer = CountVectorizer(binary = True) 
  word_tokenizer = vectorizer.build_tokenizer()
  token = [word_tokenizer(doc_str) for doc_str in data]
  # print(len(token))
  return token

In [9]:
train_data_token = get_word_token(train_data)

In [10]:
test_data_token = get_word_token(test_data)

##### **function**:
build vocab, assign a single id for each word

In [11]:
#assign a single id for each word
def get_term_dict(doc_terms_list):
  term_set_dict = {}
  for doc_terms in doc_terms_list:
    for term in doc_terms:
        term_set_dict[term] = 1
        # print(term_set_dict)
  term_set_list = sorted(term_set_dict.keys()) 
  # print(term_set_list)      
  term_set_dict = dict(zip(term_set_list, range(len(term_set_list))))
  return term_set_dict

In [12]:
'''  Test  '''
# corpus = [
# 'This is the first document.',
# 'This is the second second document.',
# 'And the third one.',
# 'Is this the first document?',
#  ]
 
# f = get_term_dict(get_word_token(corpus))
# print(f)
# f = get_term_dict(train_data)
# print(f)

'  Test  '

In [13]:
def get_class_dict(doc_class_list):
  class_dict = {}
  class_dict[0] = doc_class_list.count(0)
  class_dict[1] = doc_class_list.count(1)
  return class_dict

In [14]:
vocab_dict = get_term_dict(train_data_token)
# class_dict = get_class_dict(train_class)
# print(class_dict)
# print(vocab_dict)


##### **function**:

compute frequency for spam and legit files

In [15]:
def compute_frequency(train_data_token,train_class):
  c ={'x':train_data_token,'y':train_class}
  df = pd.DataFrame(c)
  from sklearn.utils import shuffle
  df = shuffle(df)
  vocab_dict = get_term_dict(train_data_token)#achieve word id
  
  #get spam
  df1 = df.loc[df['y']==1]
  spam_num = df1.shape[0]
  # print(spam_num)
  spams = df1['x'].values.tolist()
  # print(len(spams))
  spams_dict = set(_flatten(spams))
  # print(len(spams_dict))
  #get legit
  df0 = df.loc[df['y']==0]
  legit_num = df0.shape[0]
  legits = df0['x'].values.tolist()
  # print(legits)
  legits_dict = set(_flatten(legits))
  # print(len(legits_dict))
  
  vocab_spam = {}
  vocab_legit = {}
  #compute spam
  for word in spams_dict:
    # print(word)
    for spam in spams:
      if word in spam:
        vocab_spam[word] = vocab_spam.get(word, 0) + 1
  # print(vocab_spam)
  for word in legits_dict:
    # print(word)
    for legit in legits:
      if word in legit:
        vocab_legit[word] = vocab_legit.get(word, 0) + 1
  
  # print(vocab_legit)
  return spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit

In [16]:
spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit = compute_frequency(train_data_token,train_class)


In [17]:
spam_num_t,legit_num_t,vocab_dict_t,vocab_spam_t,vocab_legit_t = compute_frequency(test_data_token,test_class)


In [18]:
print(spam_num,legit_num)
print(vocab_dict)
print(vocab_spam)
print(vocab_legit)

432 2170
{'00': 0, '000': 1, '00003000140': 2, '00003003958': 3, '0001': 4, '00014': 5, '00036': 6, '000bp': 7, '000yen': 8, '001': 9, '0011': 10, '0014': 11, '00170': 12, '0019': 13, '00198': 14, '0027': 15, '0031': 16, '00333': 17, '0037': 18, '0039': 19, '003n7': 20, '0041': 21, '0049': 22, '0057': 23, '0067': 24, '0073': 25, '0074': 26, '008': 27, '009': 28, '00919680': 29, '00a': 30, '00am': 31, '00congress': 32, '00d': 33, '00f': 34, '00h': 35, '00hfstahlke': 36, '00i': 37, '00p': 38, '00pm': 39, '00the': 40, '00uzheb': 41, '01': 42, '01006': 43, '0106': 44, '0108': 45, '011': 46, '0118': 47, '01232': 48, '0135': 49, '0139': 50, '013953': 51, '013a': 52, '014686': 53, '0147': 54, '014796': 55, '014863': 56, '014893': 57, '014904': 58, '014979': 59, '014991': 60, '015491': 61, '015509': 62, '015679': 63, '015780': 64, '015820': 65, '016086': 66, '0161': 67, '016187': 68, '016197': 69, '016285': 70, '01701': 71, '0177': 72, '01784': 73, '0181': 74, '0182': 75, '01904': 76, '01bd835

In [19]:
print(len(vocab_dict))
print(len(vocab_spam))
print(len(vocab_legit))


51602
9998
47487



**compute IG for each word**

In [20]:
def compute_IG_word(word,spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit):
  if word in vocab_spam.keys():
    s = vocab_spam[word]
  else:
    s = 0
  if word in vocab_legit.keys():
    l = vocab_legit[word]
  else:
    l = 0
  total = spam_num+legit_num
  # print(vocab_spam[word])#4
  # print(vocab_legit[word])#51
  # print(spam_num+legit_num)#2602
  if s == 0:
    A=0
  else:
    A = (s/total)*(math.log(s/(s+l)))#spam&present:0.0060741640562358605
  # print(A)
  if (spam_num-s == 0) or (total-s-l == 0):
    B = 0
  else:
    B = ((spam_num-s)/(total))*(math.log((spam_num-s)/(total-s-l)))
  # print(B)
  if l == 0:
    C = 0
  else:
    C = (l/total)*(math.log(l/(s+l)))
  # print(C)
  if (legit_num-l==0) or (total-s-l==0):
    D = 0
  else:
    D = ((legit_num-l)/(total))*(math.log((legit_num-l)/(total-s-l)))
  # print(D)
  return -(A+B+C+D)

In [21]:
# IG_for_word = compute_IG_word('slowly',432,2170,vocab_dict,vocab_spam,vocab_legit)
# print(IG_for_word)

In [22]:
def compute_IG_dict(spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit):
  res = {}
  for word in vocab_dict.keys():
    res[word] = compute_IG_word(word,spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit)
    
  res = sorted(res.items(), key = lambda item:item[1])
  
  # print(res)

  return res

In [23]:
IG_dict = compute_IG_dict(432,2170,vocab_dict,vocab_spam,vocab_legit)
print(IG_dict)

[('language', 0.3067603560254749), ('remove', 0.33243051762615417), ('free', 0.33642552041112483), ('linguistic', 0.3433256804175116), ('university', 0.3490178273004656), ('money', 0.36726795765267584), ('click', 0.37864945333327626), ('market', 0.38540704032399575), ('our', 0.3879838770047447), ('business', 0.3893441762896718), ('today', 0.3931140202836582), ('advertise', 0.3954411338916085), ('product', 0.3959467050053215), ('company', 0.39616305584116357), ('sell', 0.3962663922243214), ('million', 0.3974351109752905), ('linguistics', 0.39748227048158463), ('english', 0.39772715090031996), ('internet', 0.39786042273675437), ('income', 0.39885109841613664), ('easy', 0.40046729654956076), ('save', 0.401494145912721), ('guarantee', 0.4018832858657611), ('thousand', 0.4020699667184648), ('best', 0.4035228519134786), ('check', 0.40385282536068023), ('purchase', 0.40460054460748196), ('buy', 0.4050977583294578), ('cash', 0.4052741864952597), ('win', 0.4053364428885521), ('day', 0.405850876

In [24]:
IG_dict_t = compute_IG_dict(spam_num_t,legit_num_t,vocab_dict_t,vocab_spam_t,vocab_legit_t)
print(IG_dict_t)

[('language', 0.25976061826519964), ('1998', 0.25992239124260613), ('university', 0.2742699003556051), ('linguistic', 0.3296946867866638), ('papers', 0.3508449610787564), ('conference', 0.35200929930266955), ('remove', 0.3674456586948345), ('research', 0.3783152679167061), ('english', 0.3797406303672646), ('study', 0.38072054255747034), ('author', 0.38553580194626547), ('wait', 0.38749392632250457), ('click', 0.3883823477702234), ('ll', 0.38892037166257126), ('workshop', 0.3911369540062285), ('abstract', 0.3929631108191859), ('sell', 0.39342193774565093), ('never', 0.39394217628871575), ('committee', 0.3947695619433619), ('discussion', 0.3947695619433619), ('enter', 0.3956690244332387), ('vacation', 0.3956690244332387), ('com', 0.3980090496772769), ('free', 0.39856162698453756), ('want', 0.3989135806219429), ('save', 0.39951176498810603), ('deadline', 0.4000748450991357), ('speaker', 0.4000748450991357), ('fax', 0.4009363090867062), ('structure', 0.4009429464884674), ('everyone', 0.402

**feature extraction and embedding**

In [25]:

feature_nums = [10, 100, 1000]
feature = []
for i in IG_dict:
  feature.append(i[0])
print(feature)
features = [0] * len(feature_nums)
print(features)
c = 0
for feature_num in feature_nums:
  features[c] = feature[:feature_num]
  c += 1
print(features[0])
print(features[1])
print(features[2]) 


['language', 'remove', 'free', 'linguistic', 'university', 'money', 'click', 'market', 'our', 'business', 'today', 'advertise', 'product', 'company', 'sell', 'million', 'linguistics', 'english', 'internet', 'income', 'easy', 'save', 'guarantee', 'thousand', 'best', 'check', 'purchase', 'buy', 'cash', 'win', 'day', 'bulk', 'over', 'want', 'cost', 'dollar', 'every', '100', 'mailing', 'edu', 'service', 'll', 'com', 'yourself', 'papers', 'linguist', 'hundred', 'theory', 'earn', 'hour', 'customer', 'abstract', 'offer', 'profit', 'success', 'conference', 'fun', 'month', 'speaker', 'yours', 'here', 'watch', 'receive', 'pay', 'bonus', 'ever', 'syntax', 'discussion', 'amaze', 'credit', 'zip', 'start', 'sale', 'live', 'investment', 'toll', 'department', 'grammar', 'financial', 'anywhere', 'online', 'dream', 'science', 'huge', 'ad', 'deadline', 'structure', 'friend', 'simply', 'mlm', 'week', 'wait', 'need', 'workshop', 'study', 'fresh', 'security', 'analysis', 'marketing', 'xxx', 'topic', 'ship',

**get the frequency embedding matrix**

In [26]:
def F_get_train_matrix(train_data_token):

  embeds0 = []
  embeds1 = []
  embeds2 = []

  for text in train_data_token:
    # print(text)
    c = 0
    embed = [0 for i in range(10)]
    for i in features[0]:
      if i in text:
        embed[c] = text.count(i)
      c += 1
    embeds0.append(embed)

  for text in train_data_token:
    # print(text)
    c = 0
    embed = [0 for i in range(100)]
    for i in features[1]:
      if i in text:
        embed[c] = text.count(i)
      c += 1
    embeds1.append(embed)

  for text in train_data_token:
    # print(text)
    c = 0
    embed = [0 for i in range(1000)]
    for i in features[2]:
      if i in text:
        embed[c] = text.count(i)
      c += 1
    embeds2.append(embed)
  return embeds0,embeds1,embeds2
#test
def F_get_train_matrix(test_data_token):
  embeds_t_0 = []
  embeds_t_1 = []
  embeds_t_2 = []

  for text in test_data_token:
    # print(text)
    c = 0
    embed = [0 for i in range(10)]
    for i in features[0]:
      if i in text:
        embed[c] = text.count(i)
      c += 1
    embeds_t_0.append(embed)

  for text in test_data_token:
    # print(text)
    c = 0
    embed = [0 for i in range(100)]
    for i in features[1]:
      if i in text:
        embed[c] = text.count(i)
      c += 1
    embeds_t_1.append(embed)

  for text in test_data_token:
    # print(text)
    c = 0
    embed = [0 for i in range(1000)]
    for i in features[2]:
      if i in text:
        embed[c] = text.count(i)
      c += 1
    embeds_t_2.append(embed)
  return embeds_t_0,embeds_t_1,embeds_t_2

**get the binary embedding matrix**

In [27]:
#train
def get_train_matrix(train_data_token):

  embeds0 = []
  embeds1 = []
  embeds2 = []

  for text in train_data_token:
    # print(text)
    c = 0
    text = set(text)
    embed = [0 for i in range(10)]
    for i in features[0]:
      if i in text:
        embed[c] = 1
      c += 1
    embeds0.append(embed)

  for text in train_data_token:
    # print(text)
    c = 0
    text = set(text)
    embed = [0 for i in range(100)]
    for i in features[1]:
      if i in text:
        embed[c] = 1
      c += 1
    embeds1.append(embed)

  for text in train_data_token:
    # print(text)
    c = 0
    text = set(text)
    embed = [0 for i in range(1000)]
    for i in features[2]:
      if i in text:
        embed[c] = 1
      c += 1
    embeds2.append(embed)
  return embeds0,embeds1,embeds2
#test
def get_train_matrix(test_data_token):
  embeds_t_0 = []
  embeds_t_1 = []
  embeds_t_2 = []

  for text in test_data_token:
    # print(text)
    c = 0
    text = set(text)
    embed = [0 for i in range(10)]
    for i in features[0]:
      if i in text:
        embed[c] = 1
      c += 1
    embeds_t_0.append(embed)

  for text in test_data_token:
    # print(text)
    c = 0
    text = set(text)
    embed = [0 for i in range(100)]
    for i in features[1]:
      if i in text:
        embed[c] = 1
      c += 1
    embeds_t_1.append(embed)

  for text in test_data_token:
    # print(text)
    c = 0
    text = set(text)
    embed = [0 for i in range(1000)]
    for i in features[2]:
      if i in text:
        embed[c] = 1
      c += 1
    embeds_t_2.append(embed)
  return embeds_t_0,embeds_t_1,embeds_t_2


In [28]:
def train_predict_B(data_train, data_test):
  train_x = data_train
  train_y = train_class
  cc = list(zip(train_x, train_y))
  random.shuffle(cc)
  train_x[:], train_y[:] = zip(*cc)
  clf = BernoulliNB().fit(train_x, train_y)
  y_pred = clf.predict(data_test).tolist()
  return y_pred
def get_p_r(y_pred):
  precision = []
  recall = []
  spam_index = [i for i in range(len(y_pred)) if y_pred[i] == 1]
  real_index = [i for i in range(len(test_class)) if test_class[i] == 1]
  count = 0
  for i in spam_index:
    if test_class[i] == 1:
      count += 1
  if y_pred.count(1) == 0:
    precision.append(0)
  else:
    precision.append(count/(y_pred.count(1)))
  count = 0
  for j in real_index:
    if y_pred[j] == 1:
      count += 1
  recall.append(count/test_class.count(1))
  return precision,recall

In [29]:
def train_predict_M(data_train, data_test):
  train_x = data_train
  train_y = train_class
  cc = list(zip(train_x, train_y))
  random.shuffle(cc)
  train_x[:], train_y[:] = zip(*cc)
  clf = MultinomialNB().fit(train_x, train_y)
  y_pred = clf.predict(data_test).tolist()
  return y_pred
def get_p_r(y_pred):
  precision = []
  recall = []
  spam_index = [i for i in range(len(y_pred)) if y_pred[i] == 1]
  real_index = [i for i in range(len(test_class)) if test_class[i] == 1]
  count = 0
  for i in spam_index:
    if test_class[i] == 1:
      count += 1
  if y_pred.count(1) == 0:
    precision.append(0)
  else:
    precision.append(count/(y_pred.count(1)))
  count = 0
  for j in real_index:
    if y_pred[j] == 1:
      count += 1
  recall.append(count/test_class.count(1))
  return precision,recall

**•	Bernoulli NB classifier with binary features;**

In [30]:
precision1 = []
recall1 = []

In [31]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = get_train_matrix(test_data_token)
y_pred = train_predict_B(embeds0,embeds_t_0)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision1.append(precision)
recall1.append(recall)

Loading dataset
[0.8695652173913043] [0.8163265306122449]


In [32]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = get_train_matrix(test_data_token)
y_pred = train_predict_B(embeds1,embeds_t_1)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision1.append(precision)
recall1.append(recall)

Loading dataset
[1.0] [0.673469387755102]


In [33]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = get_train_matrix(test_data_token)
y_pred = train_predict_B(embeds2,embeds_t_2)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision1.append(precision)
recall1.append(recall)

Loading dataset
[1.0] [0.6122448979591837]


In [34]:
precision1

[[0.8695652173913043], [1.0], [1.0]]

In [35]:
recall1

[[0.8163265306122449], [0.673469387755102], [0.6122448979591837]]

•	**Multinomial NB with binary features**

In [36]:
precision2 = []
recall2 = []

In [37]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = get_train_matrix(test_data_token)
y_pred = train_predict_M(embeds0,embeds_t_0)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision2.append(precision)
recall2.append(recall)

Loading dataset
[0.8888888888888888] [0.8163265306122449]


In [38]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = get_train_matrix(test_data_token)
y_pred = train_predict_M(embeds1,embeds_t_1)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision2.append(precision)
recall2.append(recall)

Loading dataset
[0.9782608695652174] [0.9183673469387755]


In [39]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = get_train_matrix(test_data_token)
y_pred = train_predict_M(embeds2,embeds_t_2)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision2.append(precision)
recall2.append(recall)

Loading dataset
[1.0] [0.9387755102040817]


In [40]:
precision2

[[0.8888888888888888], [0.9782608695652174], [1.0]]

In [41]:
recall2

[[0.8163265306122449], [0.9183673469387755], [0.9387755102040817]]

•	**Multinomial NB with term frequency (TF) features.**

In [42]:
precision3 = []
recall3 = []

In [43]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = F_get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = F_get_train_matrix(test_data_token)
y_pred = train_predict_M(embeds0,embeds_t_0)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision3.append(precision)
recall3.append(recall)

Loading dataset
[0.8518518518518519] [0.9387755102040817]


In [44]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = F_get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = F_get_train_matrix(test_data_token)
y_pred = train_predict_M(embeds1,embeds_t_1)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision3.append(precision)
recall3.append(recall)

Loading dataset
[0.9591836734693877] [0.9591836734693877]


In [45]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = F_get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = F_get_train_matrix(test_data_token)
y_pred = train_predict_M(embeds2,embeds_t_2)
precision,recall = get_p_r(y_pred)
print(precision,recall)
precision3.append(precision)
recall3.append(recall)

Loading dataset
[1.0] [0.9387755102040817]


**output:precision**

In [46]:
import pandas as pd
data = [precision1,precision2,precision3]
DF = pd.DataFrame(data, columns=["N=10","N=10","N=1000"],)
DF.index = ['Bernoulli NB classifier with binary features','Multinomial NB with binary features','Multinomial NB with term frequency (TF) features']

In [47]:
DF

N=10  ... N=1000
Bernoulli NB classifier with binary features      [0.8695652173913043]  ...  [1.0]
Multinomial NB with binary features               [0.8888888888888888]  ...  [1.0]
Multinomial NB with term frequency (TF) features  [0.8518518518518519]  ...  [1.0]

[3 rows x 3 columns]

**output:recall**

In [48]:
import pandas as pd
data = [recall1,recall2,recall3]
DF = pd.DataFrame(data, columns=["N=10","N=10","N=1000"],)
DF.index = ['Bernoulli NB classifier with binary features','Multinomial NB with binary features','Multinomial NB with term frequency (TF) features']

In [49]:
DF

N=10  ...                N=1000
Bernoulli NB classifier with binary features      [0.8163265306122449]  ...  [0.6122448979591837]
Multinomial NB with binary features               [0.8163265306122449]  ...  [0.9387755102040817]
Multinomial NB with term frequency (TF) features  [0.9387755102040817]  ...  [0.9387755102040817]

[3 rows x 3 columns]

#### **Support Vector Machine (SVM) based spam filter with TF**

In [76]:
precision_svm = []
recall_svm = []

In [77]:

train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = F_get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = F_get_train_matrix(test_data_token)
clf = SVC(kernel='rbf').fit(embeds0, train_class)#调参
predict = clf.predict(embeds_t_0).tolist()#训练
# print(predict)
precision,recall = get_p_r(predict)
print(precision,recall)
precision_svm.append(precision)
recall_svm.append(recall)

Loading dataset
[0.9354838709677419] [0.5918367346938775]


In [78]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = F_get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = F_get_train_matrix(test_data_token)
clf = SVC(kernel='rbf').fit(embeds1, train_class)#调参
predict = clf.predict(embeds_t_1).tolist()#训练
# print(predict)
precision,recall = get_p_r(predict)
print(precision,recall)
precision_svm.append(precision)
recall_svm.append(recall)

Loading dataset
[0.9705882352941176] [0.673469387755102]


In [79]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
embeds0,embeds1,embeds2 = F_get_train_matrix(train_data_token)
embeds_t_0,embeds_t_1,embeds_t_2 = F_get_train_matrix(test_data_token)
clf = SVC(kernel='rbf').fit(embeds2, train_class)#调参
predict = clf.predict(embeds_t_2).tolist()#训练
# print(predict)
precision,recall = get_p_r(predict)
print(precision,recall)
precision_svm.append(precision)
recall_svm.append(recall)

Loading dataset
[1.0] [0.6326530612244898]


In [80]:
precision_svm

[[0.9354838709677419], [0.9705882352941176], [1.0]]

In [84]:
import pandas as pd
data = [precision_svm,recall_svm]
DF = pd.DataFrame(data, columns=["N=10","N=10","N=1000"],)
DF.index = ['precision_svm','recall_svm']

In [85]:
DF

N=10                  N=10                N=1000
precision_svm  [0.9354838709677419]  [0.9705882352941176]                 [1.0]
recall_svm     [0.5918367346938775]   [0.673469387755102]  [0.6326530612244898]